# Prerequisites

Isolation settings – Your database must be set to snapshot isolation. Databases created in the PREVIEW_2023 track are snapshot isolation by default. Isolation settings can be changed by using the ISOLATION keyword in the CREATE DATABASE or ALTER DATABASE statements.

For Amazon Redshift Serverless preview: 
Creating a preview workgroup - https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-workgroup-preview.html

For Amazon Redshift provisioned clusters preview: 
Creating a preview cluster - https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#cluster-preview

Documentation link: https://docs.aws.amazon.com/redshift/latest/dg/multi-warehouse-writes-data-sharing.html#within-account-writes-share-consumer-create-database

### Create datashare on PRODUCER

[PUBLICACCESSIBLE = TRUE] values is optional

[[SET] PUBLICACCESSIBLE]
A clause that specifies whether the datashare can be shared to clusters that are publicly accessible.
The default value for SET PUBLICACCESSIBLE is FALSE.

In [0]:
CREATE DATASHARE my_datashare;

### create schemas and provide grants for datashare

In [0]:
CREATE SCHEMA myshared_schema1;
CREATE SCHEMA myshared_schema2;
 
GRANT USAGE ON SCHEMA myshared_schema1 TO DATASHARE my_datashare;
GRANT CREATE, USAGE ON SCHEMA myshared_schema2 TO DATASHARE my_datashare;

### TPCDS data sets which can be used
https://github.com/awslabs/amazon-redshift-utils/blob/master/src/CloudDataWarehouseBenchmark/Cloud-DWB-Derived-from-TPCDS/1TB/ddl.sql

In [0]:
-- Tables that can be used for demo
create table myshared_schema1.customer_address
(
 ca_address_sk int4 not null ,
  ca_address_id char(16) not null ,
  ca_street_number char(10) ,      
  ca_street_name varchar(60) ,   
  ca_street_type char(15) ,     
  ca_suite_number char(10) ,    
  ca_city varchar(60) ,         
  ca_county varchar(30) ,       
  ca_state char(2) ,            
  ca_zip char(10) ,             
  ca_country varchar(20) ,      
  ca_gmt_offset numeric(5,2) ,  
  ca_location_type char(20)     
  ,primary key (ca_address_sk)
) distkey(ca_address_sk);

create table myshared_schema1.customer_demographics
(
  cd_demo_sk int4 not null ,   
  cd_gender char(1) ,          
  cd_marital_status char(1) ,   
  cd_education_status char(20) , 
  cd_purchase_estimate int4 ,   
  cd_credit_rating char(10) ,   
  cd_dep_count int4 ,             
  cd_dep_employed_count int4 ,    
  cd_dep_college_count int4       
  ,primary key (cd_demo_sk)
)distkey (cd_demo_sk);

create table myshared_schema1.date_dim
(
    d_date_sk                 integer               not null,
    d_date_id                 char(16)              not null,
    d_date                    date,
    d_month_seq               integer                       ,
    d_week_seq                integer                       ,
    d_quarter_seq             integer                       ,
    d_year                    integer                       ,
    d_dow                     integer                       ,
    d_moy                     integer                       ,
    d_dom                     integer                       ,
    d_qoy                     integer                       ,
    d_fy_year                 integer                       ,
    d_fy_quarter_seq          integer                       ,
    d_fy_week_seq             integer                       ,
    d_day_name                char(9)                       ,
    d_quarter_name            char(6)                       ,
    d_holiday                 char(1)                       ,
    d_weekend                 char(1)                       ,
    d_following_holiday       char(1)                       ,
    d_first_dom               integer                       ,
    d_last_dom                integer                       ,
    d_same_day_ly             integer                       ,
    d_same_day_lq             integer                       ,
    d_current_day             char(1)                       ,
    d_current_week            char(1)                       ,
    d_current_month           char(1)                       ,
    d_current_quarter         char(1)                       ,
    d_current_year            char(1)                       ,
    primary key (d_date_sk)
) diststyle all;

create table myshared_schema2.time_dim
(
    t_time_sk                 integer               not null,
    t_time_id                 char(16)              not null,
    t_time                    integer                       ,
    t_hour                    integer                       ,
    t_minute                  integer                       ,
    t_second                  integer                       ,
    t_am_pm                   char(2)                       ,
    t_shift                   char(20)                      ,
    t_sub_shift               char(20)                      ,
    t_meal_time               char(20)                      ,
    primary key (t_time_sk)
) diststyle all;

create table myshared_schema2.item
(
i_item_sk int4 not null,                     
  i_item_id char(16) not null ,      
  i_rec_start_date date,             
  i_rec_end_date date,               
  i_item_desc varchar(200) ,         
  i_current_price numeric(7,2),      
  i_wholesale_cost numeric(7,2),     
  i_brand_id int4,                   
  i_brand char(50) ,                 
  i_class_id int4,                   
  i_class char(50) ,                 
  i_category_id int4,                
  i_category char(50) ,              
  i_manufact_id int4,                
  i_manufact char(50) ,              
  i_size char(20) ,                  
  i_formulation char(20) ,           
  i_color char(20) ,            
  i_units char(10),             
  i_container char(10),         
  i_manager_id int4,            
  i_product_name char(50)       
  ,primary key (i_item_sk)
) distkey(i_item_sk) sortkey(i_category);

create table myshared_schema2.store
(
    s_store_sk                integer               not null,
    s_store_id                char(16)              not null,
    s_rec_start_date          date,
    s_rec_end_date            date,
    s_closed_date_sk          integer                       ,
    s_store_name              varchar(50)                   ,
    s_number_employees        integer                       ,
    s_floor_space             integer                       ,
    s_hours                   char(20)                      ,
    s_manager                 varchar(40)                   ,
    s_market_id               integer                       ,
    s_geography_class         varchar(100)                  ,
    s_market_desc             varchar(100)                  ,
    s_market_manager          varchar(40)                   ,
    s_division_id             integer                       ,
    s_division_name           varchar(50)                   ,
    s_company_id              integer                       ,
    s_company_name            varchar(50)                   ,
    s_street_number           varchar(10)                   ,
    s_street_name             varchar(60)                   ,
    s_street_type             char(15)                      ,
    s_suite_number            char(10)                      ,
    s_city                    varchar(60)                   ,
    s_county                  varchar(30)                   ,
    s_state                   char(2)                       ,
    s_zip                     char(10)                      ,
    s_country                 varchar(20)                   ,
    s_gmt_offset              decimal(5,2)                  ,
    s_tax_precentage          decimal(5,2)                  ,
    primary key (s_store_sk)
) diststyle all;

create table myshared_schema2.customer
(
  c_customer_sk int4 not null ,                 
  c_customer_id char(16) not null ,             
  c_current_cdemo_sk int4 ,   
  c_current_hdemo_sk int4 ,   
  c_current_addr_sk int4 ,    
  c_first_shipto_date_sk int4 ,                 
  c_first_sales_date_sk int4 ,
  c_salutation char(10) ,     
  c_first_name char(20) ,     
  c_last_name char(30) ,      
  c_preferred_cust_flag char(1) ,               
  c_birth_day int4 ,          
  c_birth_month int4 ,        
  c_birth_year int4 ,         
  c_birth_country varchar(20) ,                 
  c_login char(13) ,          
  c_email_address char(50) ,  
  c_last_review_date_sk int4 ,
  primary key (c_customer_sk)
) distkey(c_customer_sk);

create table myshared_schema2.store_sales
(
ss_sold_date_sk int4 ,            
  ss_sold_time_sk int4 ,     
  ss_item_sk int4 not null ,      
  ss_customer_sk int4 ,           
  ss_cdemo_sk int4 ,              
  ss_hdemo_sk int4 ,         
  ss_addr_sk int4 ,               
  ss_store_sk int4 ,           
  ss_promo_sk int4 ,           
  ss_ticket_number int8 not null,        
  ss_quantity int4 ,           
  ss_wholesale_cost numeric(7,2) ,          
  ss_list_price numeric(7,2) ,              
  ss_sales_price numeric(7,2) ,
  ss_ext_discount_amt numeric(7,2) ,             
  ss_ext_sales_price numeric(7,2) ,              
  ss_ext_wholesale_cost numeric(7,2) ,           
  ss_ext_list_price numeric(7,2) ,               
  ss_ext_tax numeric(7,2) ,                 
  ss_coupon_amt numeric(7,2) , 
  ss_net_paid numeric(7,2) ,   
  ss_net_paid_inc_tax numeric(7,2) ,             
  ss_net_profit numeric(7,2)                     
  ,primary key (ss_item_sk, ss_ticket_number)
) distkey(ss_item_sk) sortkey(ss_sold_date_sk);


copy myshared_schema1.customer_address from 's3://redshift-downloads/TPC-DS/2.13/1TB/customer_address/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema1.customer_demographics from 's3://redshift-downloads/TPC-DS/2.13/1TB/customer_demographics/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema1.date_dim from 's3://redshift-downloads/TPC-DS/2.13/1TB/date_dim/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema2.customer from 's3://redshift-downloads/TPC-DS/2.13/1TB/customer/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema2.store from 's3://redshift-downloads/TPC-DS/2.13/1TB/store/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema2.item from 's3://redshift-downloads/TPC-DS/2.13/1TB/item/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema2.store_sales from 's3://redshift-downloads/TPC-DS/2.13/1TB/store_sales/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy myshared_schema2.time_dim from 's3://redshift-downloads/TPC-DS/2.13/1TB/time_dim/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';



select count(*) from myshared_schema1.customer_address;  -- 6000000
select count(*) from myshared_schema1.customer_demographics;  -- 1920800
select count(*) from myshared_schema1.date_dim;  -- 73049
select count(*) from myshared_schema2.store;  -- 1002
select count(*) from myshared_schema2.item;  -- 287999764
select count(*) from myshared_schema2.store_sales;  -- 2879987999
select count(*) from myshared_schema2.time_dim;  -- 86400

### Providing necessary access on tables to datashare

Below are tables from TPCDS benchmark data sets that are available towards end use or choose which would fit your scenario
customer;  -- 12000000

customer_address;  -- 6000000

customer_demographics;  -- 1920800

date_dim;  -- 73049

store;  -- 1002

store_returns;  -- 287999764

store_sales;  -- 2879987999

time_dim;  -- 86400

### Note: Use any of the above tables to be created in myshared_schema1 and myshared_schema2. And table1/table2 can be any one of the above tables.

In [0]:
GRANT SELECT, INSERT ON TABLE myshared_schema1.date_dim, myshared_schema1.customer_address, myshared_schema2.item
TO DATASHARE my_datashare;
                     
GRANT ALL ON TABLE myshared_schema2.time_dim,myshared_schema2.region TO DATASHARE my_datashare;

### Get PRODUCER Namespace

In [0]:
SELECT current_namespace;

### Grant usage of datashare to consumer name space

In [0]:
GRANT USAGE ON DATASHARE my_datashare TO NAMESPACE 'CONSUMER_NAMESPACE';

### Get PRODUCER Namespace

## Permissions you can grant to datashares
Different object types and various permissions you can grant to them in a data sharing context.

Schemas:
USAGE and CREATE

Tables:
SELECT, INSERT, UPDATE, DELETE, TRUNCATE, DROP and REFERENCES

Functions:
EXECUTE

### Get datashare details

In [0]:
show datashares;

select * from SVV_DATASHARE_OBJECTS;